# Ví dụ giải phương trình bằng cách thử dần

Phương pháp tính thử dần được dùng nhiều trong kĩ thuật. Chẳng hạn, các bài toán truyền sóng biển thường liên quan đến "hệ thức phân tán" (dispersion relationship):

$$ L = L_0 \tanh \frac{2\pi h}{L} $$

trong đó $h$ là độ sâu nước, $L_0$ là chiều dài sóng tại vùng "nước sâu" (tại đó $h \to \infty$). Yêu cầu tính ra chiều dài sóng $L$ tại độ sâu $h$. 

Do $L$ có mặt ở cả hai vế phương trình (không thể đưa về một vế được) nên cần phải giải bằng phương pháp gần đúng. Ở đây giải bằng cách thử dần (gần đúng liên tiếp, successive approximation).

Mã lệnh chương trình Julia dưới đây minh họa một hàm có tên `giải` với:
* các biến số đầu vào `h` và `L0`
* kết quả tính ra `L` được trả lại (`return`) ở cuối hàm.

Phương pháp tính toán là tính lặp. Qua mỗi lần lặp sẽ so sánh sai số tương đối với một số định trước, ở đây tạm lấy là 0.00001 (vốn là quá tốt đối với các bài toán kĩ thuật).

In [8]:
function giải(h::Number, L₀::Number)
    L = L₀
    sai_số = Inf
    while sai_số > 0.00001
        L₁ = L₀ * tanh(2π*h/L)
        sai_số = abs(L₁ - L)/L
        L = L₁
    end
    return L
end

giải (generic function with 1 method)

Như có thể thấy từ đoạn mã lệnh trên, ta có thể đặt tên các biến số bằng chữ có dấu và có thể dùng kí hiệu đặc biệt, chẳng hạn các chỉ số khi đặt tên biến như L0 và L1. Ngoài ra, ngôn ngữ Julia có sẵn các giá trị đặc biệt, chẳng hạn $\pi$ và `Inf` (vô cùng), cũng như các hàm toán học (`tanh`, `abs` (trị tuyệt đối)).

Ta thử dùng hàm vừa lập để tính cho 2 trường hợp: 
* h = 5 m, L0 = 100 m
* h = 3 m, L0 = 100 m

In [9]:
giải(5, 100)

53.10377348111278

In [10]:
giải(3, 100)

42.048693156165214

Rõ ràng kết quả cho thấy: cùng với một điều kiện sóng nước sâu thì vào đến vùng nước càng nông, chiều dài sóng (bước sóng) càng co ngắn lại.

Nhưng có thể cải tiến được phương pháp tính toán không? Để biết được việc tính toán hiệu quả hay không thì cần đánh giá số lần lặp và sai số sau mỗi lần lặp.

Ta đặt thêm các lệnh in các cặp giá trị `lần_lặp` và `sai_số`. Trong Julia, lệnh in (đúng hơn là "hàm in") là `println()` với biến số cần in đặt trong cặp ngoặc.

In [19]:
function giải(h::Number, L₀::Number)
    L = L₀
    sai_số = Inf
    lần_lặp = 0
    while sai_số > 0.00001
        L₁ = L₀ * tanh(2π*h/L)
        sai_số = abs(L₁ - L)/L
        lần_lặp += 1
        println(lần_lặp, " ", sai_số)
        L = L₁ 
    end
    return L
end

giải (generic function with 1 method)

In [20]:
giải(5, 100)

1 0.6957838071132555
2 1.5474733999372763
3 0.5038091040548285
4 0.7512392882631744
5 0.3534834164499652
6 0.41919720639755814
7 0.241397563706804
8 0.24833927150277194
9 0.1614939267497295
10 0.1517812507405171
11 0.10645550520078569
12 0.09442624087744932
13 0.06946358050873311
14 0.05936847495811449
15 0.04501663476518041
16 0.03756887456225652
17 0.02904185590647517
18 0.023869794867281788
19 0.018680663677875735
20 0.015204365236918482
21 0.01199300429452992
22 0.009700259098304314
23 0.0076900042244049055
24 0.006194983773951215
25 0.004926966623870965
26 0.00395893523701923
27 0.003155083044593136
28 0.0025310232291497078
29 0.0020197596701233165
30 0.0016185588758523609
31 0.001292699079324543
32 0.001035223517531377
33 0.0008272500583429719
34 0.0006621960577684028
35 0.0005293449844636564
36 0.0004236127290680409
37 0.0003387013127602889
38 0.0002710007967013429
39 0.00021671034859602477
40 0.0001733741666040568
41 0.00013865407154170617
42 0.0001109190250387064
43 8.87113802

53.10377348111278

Như vậy là cần đến 53 vòng lặp mới đảm bảo sai số tương đối nhỏ hơn 0.00001 hay $10 \times 10^{-6}$. Trong Julia, kí hiệu `e-N` được sử dụng. `9.5e-6` là $9.5 \times 10^{-6}$.

Liệu có cách nào giải nhanh hơn không? Ta hãy lập một hàm khác, tên là `giải2`, trong đó giá trị chiều dài sóng được cập nhật là trung bình cộng của giá trị mới tính toán và giá trị cũ. Nói cách khác, cập nhật `L = 0.5(L₁ + L)` thay vì `L = L₁`.

In [17]:
function giải₂(h::Number, L₀::Number)
    L = L₀
    sai_số = Inf
    lần_lặp = 0
    while sai_số > 0.00001
        L₁ = L₀ * tanh(2π*h/L)
        sai_số = abs(L₁ - L)/L
        lần_lặp += 1
        println(lần_lặp, " ", sai_số)
        L = 0.5(L₁ + L) 
    end
    return L
end

giải₂ (generic function with 1 method)

In [18]:
giải₂(5, 100)

1 0.6957838071132555
2 0.31353156896241346
3 0.061012030206049256
4 0.006964392992138756
5 0.00070753000793675
6 7.090908764935875e-5
7 7.096718213651491e-6


53.10401886379769

Rõ ràng, cách làm này nhanh hơn hẳn. Và phép xấp xỉ kết thúc sau 7 lần lặp.

Như vậy bằng Julia ta có thể thực hiện và đánh giá hiệu quả của phương pháp số. Mã lệnh thường được tổ chức dưới dạng các hàm (`function`). Việc tính toán được thực hiện bằng cách gọi hàm, áp dụng cho các bộ tham số khác nhau. Trong các bài tiếp theo ta sẽ thực hiện các phép toán với vec tơ, ma trận và vẽ đồ thị.